In [1]:
import numpy as np
import pandas as pd
import re
import pandas_profiling
import numbers
from spellchecker import SpellChecker
from word2number import w2n

In [2]:
train = pd.read_csv('data/train.csv')
test = pd.read_csv('data/test.csv')
spell = SpellChecker()

In [3]:
profile = train.profile_report(title='Medical Record Profiling Report')
profile.to_file(output_file="train_data_summary.html")

/anaconda3/lib/python3.7/site-packages/pandas_profiling/model/correlations.py:124: UserWarning: There was an attempt to calculate the cramers correlation, but this failed.
To hide this warning, disable the calculation
(using `df.profile_report(correlations={"cramers": False}`)
If this is problematic for your use case, please report this as an issue:
https://github.com/pandas-profiling/pandas-profiling/issues
(include the error message: 'The internally computed table of expected frequencies has a zero element at (0, 3).')
  correlation_name=correlation_name, error=error


In [4]:
train.profile_report(style={'full_width':True})

/anaconda3/lib/python3.7/site-packages/pandas_profiling/model/correlations.py:124: UserWarning: There was an attempt to calculate the cramers correlation, but this failed.
To hide this warning, disable the calculation
(using `df.profile_report(correlations={"cramers": False}`)
If this is problematic for your use case, please report this as an issue:
https://github.com/pandas-profiling/pandas-profiling/issues
(include the error message: 'The internally computed table of expected frequencies has a zero element at (0, 3).')
  correlation_name=correlation_name, error=error


In [5]:
pandas_profiling.ProfileReport(train)

/anaconda3/lib/python3.7/site-packages/pandas_profiling/model/correlations.py:124: UserWarning: There was an attempt to calculate the cramers correlation, but this failed.
To hide this warning, disable the calculation
(using `df.profile_report(correlations={"cramers": False}`)
If this is problematic for your use case, please report this as an issue:
https://github.com/pandas-profiling/pandas-profiling/issues
(include the error message: 'The internally computed table of expected frequencies has a zero element at (0, 3).')
  correlation_name=correlation_name, error=error


In [6]:
train["BMI"] = pd.to_numeric(train["BMI"],errors='coerce')

In [7]:
train["sex_and_age"].value_counts()
#%zz
def is_number(s):
    """ Returns True is string is a number. """
    try:
        float(s)
        return True
    except ValueError:
        return False

F, 54         345
F, 55         323
F, 53         322
F, 56         319
F, 51         314
F, 60         308
F, 41         307
F, 82         304
F, 50         303
F, 81         296
F, 34         294
F, 32         292
F, 52         291
F, 47         290
F, 48         289
F, 58         289
F, 40         289
F, 59         287
F, 46         286
F, 57         283
F, 44         282
F, 49         281
F, 30         279
F, 45         277
F, 65         276
F, 64         271
F, 31         271
F, 83         270
F, 26         270
F, 28         263
             ... 
m, 22           1
4.72, F         1
4.32, M         1
F, eleven       1
m, 8            1
M, six          1
4.16, F         1
3.72, M         1
Other, 13       1
4.56, M         1
f, 27           1
4.64, F         1
F, twenty       1
female, 8       1
MALE, 59        1
m, 25           1
female, 72      1
mmale, 75       1
4.24, M         1
F, seven        1
3.8, M          1
M, fifty        1
F, fifty        1
3.24, M         1
4, M      

In [38]:
# Process gender into oneof "F", "M" and "OTHER"
def genderSpellingRewrite(gender_str):
    if not isinstance(gender_str, str):
        return None;
    uppered = gender_str.upper()
    # Repeated single occurence should be truncate.
    patternM = re.compile('[M]+$')
    if (patternM.match(uppered)):
        return "M"
    patternF = re.compile('[F]+$')
    if (patternF.match(uppered)):
        return "F"
    # Misspelling should be corrected and replaced.
    # TODO: Malle is not going to be corrected as Male.Need to update spell's known list.
    corrected = spell.correction(uppered).upper()
    if (corrected == "FEMALE"):
        return "F"
    if (corrected == "MALE"):
        return "M"
    if (corrected == "OTHER"):
        return "OTHER"
    return None


In [39]:
# Process human number word into number
def numberConversion(potential_number_word):
    # Correct any possible miss spelled number_word
    corrected_potential_word = spell.correction(potential_number_word)
    # check it it means number
    try:
      potential_num = w2n.word_to_num(corrected_potential_word)
    except ValueError:
        return potential_number_word
    return potential_num

In [40]:
print(numberConversion("9"))

9


In [72]:
def formatSexAge(origin_str):
    if not isinstance(origin_str, str):
        return [None,None]
    # Preprocess 
    # Entry with missing column.
    if (',' not in origin_str):
        origin_str = origin_str + ',';
    origin_list = origin_str.replace(" ", "").upper().split(",")
    if(origin_list[0].upper() == "NAN"):
        origin_list[0] = ""
    if(origin_list[1].upper() == "NAN"):
        origin_list[1] = ""
    # Convert possible number in entry.
    if((not is_number(origin_list[0])) and (not is_number(origin_list[1]))):
        origin_list[0] = numberConversion(origin_list[0])
        origin_list[1] = numberConversion(origin_list[1])
    genderSet = set(['F', 'M', 'OTHER'])
    if (is_number(origin_list[0])):
        # wrong entry (num, num)
        if (is_number(origin_list[1])):
            if (origin_list[0] == origin_list[1]):
                return [None, origin_list[0]]
            return [None, None]
        else: # first number, second '' or gender (NOT num for sure)
          # swap back number
          origin_list = origin_list[::-1]
          origin_list[0] = genderSpellingRewrite(origin_list[0])
          return origin_list
    else: 
        origin_list[0] = genderSpellingRewrite(origin_list[0])
         # first '' or str, second is number
        if (is_number(origin_list[1])):
            return origin_list
        else:
            origin_list[1] = genderSpellingRewrite(origin_list[1])
            if(origin_list[0] == origin_list[1]):
               origin_list[1] = None
            return origin_list


In [100]:
train["sex_age_list"] = train["sex_and_age"].astype(str).apply(lambda x: formatSexAge(x))
train[['sex','age']] = pd.DataFrame(train["sex_age_list"].values.tolist(), index= train.index)

In [101]:
train["sex"].value_counts()

F        20557
M        14271
OTHER        7
Name: sex, dtype: int64